# IBM Data Science Coursera Capstone Project

# Table of Contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)
___

# Introduction: Business Problem<a id='introduction'></a>

Jakarta is the capital of Indonesia with a population of 10,5 million, and is the heart of the second densest metropolitan area in the world behind Tokyo, Japan. Having hosted ASEAN games recently back in 2018, it has witnessed heavy investment in transportational infrastructure with the opening of the first MRT line in Indonesia just this year.

Given that, the city will surely see more growth of which information regarding the lay of the land will be invaluable for investors and entrepreneurs to make strategic decision for investment or choosing locations for business operation.

This project will attempt to explore patterns of subdistricts within Jakarta by categorizing them into clusters in order to identify existing trends within neighborhoods of Jakarta. From there on, recommendations can be made on which category of neighborhood will be most suitable for a certain type of venue to be opened.

The result of this project is aimed at general entrepreneur but may be most useful for entrepreneurs on the food and beverage sector given that location can be the deciding factor for a success.
___

# Data<a id='data'></a>

To analyze trends in Jakarta's subdistrict, the list of subdistrict is obtained from [Jakarta subdistrict wikipedia page](https://en.wikipedia.org/wiki/Subdistricts_of_Jakarta).

Venue queries will then be made by subdistricts using FourSquare APIs. The resulting data regarding venue category will be used to observe commonality between subdistricts. The commonality clusters can then provide insight on which type of venue will thrive better on which cluster. K-means clustering algorithm will be used to find pattern between the subdistricts.

In summary, the following data is required to meet the objective:

- Subdistricts of Jakarta
- Coordinates of these subdistricts
- Trending Venues on the area
- Venue categories

___

## Data Gathering

Initialize required library.

In [1]:
# Load needed libraries for data collection

# HTML request and scraper library
import requests
from bs4 import BeautifulSoup

# Geocoding library
#!conda install -c conda-forge geopy --yes # Unquote to install geopy
from geopy.geocoders import ArcGIS # module to convert an address into latitude and longitude values

# Library for data analysis
import pandas as pd
from pandas.io.json import json_normalize # Function to transform json
import numpy as np

#!conda install -c conda-forge folium=0.5.0 --yes # Unquote to install folium
import folium # map plotting library
import matplotlib.cm as cm
import matplotlib.colors as colors

# Import collapsible JSON for exploration
from IPython.display import JSON

# k-means for categorization
from sklearn.cluster import KMeans

# Pretty print
from pprint import pprint

Parse Jakarta's subdistrict from the wiki page.

In [2]:
# Scraped list of subdistricts from wikipedia

page = requests.get("https://en.wikipedia.org/wiki/Subdistricts_of_Jakarta")
soup = BeautifulSoup(page.content, 'html.parser')

# Parse soup for subdistrict
subdistrict =[i.text for i in soup.select('table.multicol tbody tr td ul li') if len(i.text) < 50]

pprint(subdistrict)

['Cengkareng',
 'Grogol Petamburan',
 'Kalideres',
 'Kebon Jeruk',
 'Kembangan',
 'Palmerah',
 'Taman Sari',
 'Tambora',
 'Cempaka Putih',
 'Gambir',
 'Johar Baru',
 'Kemayoran',
 'Sawah Besar',
 'Senen',
 'Tanah Abang',
 'Cilandak',
 'Jagakarsa',
 'Kebayoran Baru',
 'Kebayoran Lama',
 'Mampang Prapatan',
 'Pancoran',
 'Pasar Minggu',
 'Pesanggrahan',
 'Setiabudi',
 'Tebet',
 'Cakung',
 'Cipayung',
 'Ciracas',
 'Duren Sawit',
 'Jatinegara',
 'Kramat Jati',
 'Makasar',
 'Matraman',
 'Menteng',
 'Pasar Rebo',
 'Pulo Gadung',
 'Cilincing',
 'Kelapa Gading',
 'Koja',
 'Pademangan',
 'Penjaringan',
 'Tanjung Priok',
 'Kepulauan Seribu Selatan',
 'Kepulauan Seribu Utara']


In [3]:
# Obtain geocoding for each

arcg = ArcGIS() #instantiate the geolocator from geopy
subdist_coord = {} 


# Define a function to query coordinates
def get_coord_jkt(addr):
    'Take a list of address and return a dictionary of address-coordinate pair'
    dic = {}
    for i in addr:
        try:
            location = arcg.geocode(i+", Jakarta") # Query the address geocode with added Jakarta as a specifier
            print(i, "queried, returned as",location[0]) # Check
            dic[i] = location[1]
        except Exception as E:
            print("ERROR: occured at", i, E)
    print("Query complete, total query:", len(addr))
    return dic

subdistcoord = get_coord_jkt(subdistrict)
pprint(subdistcoord)

Cengkareng queried, returned as Cengkareng, Jakarta, DKI Jakarta
Grogol Petamburan queried, returned as Grogol Petamburan, Jakarta, DKI Jakarta
Kalideres queried, returned as Kalideres, Jakarta, DKI Jakarta
Kebon Jeruk queried, returned as Kebon Jeruk, Jakarta, DKI Jakarta
Kembangan queried, returned as Kembangan, Jakarta, DKI Jakarta
Palmerah queried, returned as Palmerah, Jakarta, DKI Jakarta
Taman Sari queried, returned as Taman Sari, Tamansari, Jakarta, DKI Jakarta
Tambora queried, returned as Tambora, Jakarta, DKI Jakarta
Cempaka Putih queried, returned as Cempaka Putih, Jakarta, DKI Jakarta
Gambir queried, returned as Gambir, Jakarta, DKI Jakarta
Johar Baru queried, returned as Johar Baru, Jakarta, DKI Jakarta
Kemayoran queried, returned as Kemayoran, Jakarta, DKI Jakarta
Sawah Besar queried, returned as Sawah Besar, Jakarta, DKI Jakarta
Senen queried, returned as Senen, Jakarta, DKI Jakarta
Tanah Abang queried, returned as Tanah Abang, Jakarta, DKI Jakarta
Cilandak queried, retu

In [4]:
# Put the dictionary into data frame
jakarta_df = pd.DataFrame.from_dict(subdistcoord, orient='index', columns=['Latitude','Longitude'])
jakarta_df

Latitude  Longitude
Cengkareng                -6.13060  106.74559
Grogol Petamburan         -6.16777  106.78457
Kalideres                 -6.12210  106.70727
Kebon Jeruk               -6.19702  106.77308
Kembangan                 -6.21823  106.73749
Palmerah                  -6.19153  106.79556
Taman Sari                -6.15327  106.82357
Tambora                   -6.15194  106.80777
Cempaka Putih             -6.17600  106.87060
Gambir                    -6.17299  106.81571
Johar Baru                -6.18589  106.85593
Kemayoran                 -6.16584  106.85396
Sawah Besar               -6.15741  106.83140
Senen                     -6.19675  106.84848
Tanah Abang               -6.20784  106.81083
Cilandak                  -6.29051  106.79491
Jagakarsa                 -6.34325  106.81725
Kebayoran Baru            -6.25146  106.79748
Kebayoran Lama            -6.26385  106.77519
Mampang Prapatan          -6.24523  106.83149
Pancoran                  -6.25548  106.84391
Pasar Minggu              -6.29265  106.82791
Pesanggrahan              -6.23637  106.75452
Setiabudi                 -6.22124  106.82528
Tebet                     -6.22939  106.84971
Cakung                    -6.19651  106.93520
Cipayung                  -6.32673  106.90298
Ciracas                   -6.32879  106.88475
Duren Sawit               -6.23501  106.92261
Jatinegara                -6.23265  106.88539
Kramat Jati               -6.27074  106.86738
Makasar                   -6.28508  106.90214
Matraman                  -6.19983  106.86268
Menteng                   -6.20309  106.83799
Pasar Rebo                -6.33769  106.85755
Pulo Gadung               -6.18039  106.89897
Cilincing                 -6.11374  106.94934
Kelapa Gading             -6.16021  106.90478
Koja                      -6.12716  106.89919
Pademangan                -6.13437  106.83658
Penjaringan               -6.11662  106.77803
Tanjung Priok             -6.12842  106.85952
Kepulauan Seribu Selatan  -5.79733  106.49630
Kepulauan Seribu Utara    -5.74537  106.61380

As we are more interested in the city area, drop the 2 island subdistricts from the data frame.

Also convert dataframe's index into its own column as *Subdistrict*.

In [5]:
# Drop 2 subdistrict which is located on a separate island and turn index into its own column
k = ['Kepulauan' in i for i in jakarta_df.index] 
pd.Series(k)
jakarta_df.drop(jakarta_df[k].index, inplace=True)

# Convert index to its own column under Subdistrict
jakarta_df.reset_index(inplace=True)
jakarta_df.columns = ['Subdistrict','Latitude','Longitude']
jakarta_df

Subdistrict  Latitude  Longitude
0          Cengkareng  -6.13060  106.74559
1   Grogol Petamburan  -6.16777  106.78457
2           Kalideres  -6.12210  106.70727
3         Kebon Jeruk  -6.19702  106.77308
4           Kembangan  -6.21823  106.73749
5            Palmerah  -6.19153  106.79556
6          Taman Sari  -6.15327  106.82357
7             Tambora  -6.15194  106.80777
8       Cempaka Putih  -6.17600  106.87060
9              Gambir  -6.17299  106.81571
10         Johar Baru  -6.18589  106.85593
11          Kemayoran  -6.16584  106.85396
12        Sawah Besar  -6.15741  106.83140
13              Senen  -6.19675  106.84848
14        Tanah Abang  -6.20784  106.81083
15           Cilandak  -6.29051  106.79491
16          Jagakarsa  -6.34325  106.81725
17     Kebayoran Baru  -6.25146  106.79748
18     Kebayoran Lama  -6.26385  106.77519
19   Mampang Prapatan  -6.24523  106.83149
20           Pancoran  -6.25548  106.84391
21       Pasar Minggu  -6.29265  106.82791
22       Pesanggrahan  -6.23637  106.75452
23          Setiabudi  -6.22124  106.82528
24              Tebet  -6.22939  106.84971
25             Cakung  -6.19651  106.93520
26           Cipayung  -6.32673  106.90298
27            Ciracas  -6.32879  106.88475
28        Duren Sawit  -6.23501  106.92261
29         Jatinegara  -6.23265  106.88539
30        Kramat Jati  -6.27074  106.86738
31            Makasar  -6.28508  106.90214
32           Matraman  -6.19983  106.86268
33            Menteng  -6.20309  106.83799
34         Pasar Rebo  -6.33769  106.85755
35        Pulo Gadung  -6.18039  106.89897
36          Cilincing  -6.11374  106.94934
37      Kelapa Gading  -6.16021  106.90478
38               Koja  -6.12716  106.89919
39         Pademangan  -6.13437  106.83658
40        Penjaringan  -6.11662  106.77803
41      Tanjung Priok  -6.12842  106.85952

Draw them on a map to verify.

In [6]:
# Draw the map centered on Jakarta
jakarta = get_coord_jkt(["DKI Jakarta"])
jktmap = folium.Map(location=jakarta["DKI Jakarta"], zoom_start=11) 

# Add a red circle marker to represent the center of Jakarta
folium.CircleMarker(
    jakarta["DKI Jakarta"],
    radius=10,
    color='red',
    popup='Jakarta',
    fill = True,
    fill_color = 'red',
    fill_opacity = 1
    ).add_to(jktmap)

# Add the subdistricts as blue circle markers
for subdist, coord in subdistcoord.items():
    folium.CircleMarker(
        coord,
        radius=5,
        color='blue',
        popup=subdist,
        fill = True,
        fill_color='blue',
        fill_opacity=1
    ).add_to(jktmap)

# display map
jktmap

DKI Jakarta queried, returned as Jakarta, DKI Jakarta
Query complete, total query: 1


Having the subdistricts geocoded, it is time for us to pull venue data on each subdistrict using FourSquare API.

## FourSquare call

Add all credentials.

In [9]:
CLIENT_ID = '5DUR252JEQWBIYILVBDTQ33IUY5FZG2ATYSTZVR5XYSMFBGR' # your Foursquare ID
CLIENT_SECRET = 'VESG00GQDAW23EAXWHUTBA1H5DKUICWX3WSRKJ5CAMWGN44T' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 100
print('Your credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentials:
CLIENT_ID: 5DUR252JEQWBIYILVBDTQ33IUY5FZG2ATYSTZVR5XYSMFBGR
CLIENT_SECRET:VESG00GQDAW23EAXWHUTBA1H5DKUICWX3WSRKJ5CAMWGN44T


Check Gambir area to verify

In [7]:
# Check Gambir area recommended venues
latitude = jakarta_df['Latitude'][9]
longitude = jakarta_df['Longitude'][9]
radius = 1500

In [10]:
# Import collapsible JSON for exploration
from IPython.display import JSON

# define URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)

# send GET request and get recommended venues
results = requests.get(url).json()
print('There are {} recommended venues.'.format(len(results['response']['groups'][0]['items'])))

JSON(results)

There are 100 recommended venues.


<IPython.core.display.JSON object>

Process and convert JSON response into a dataframe.

In [11]:
# Part adapted from example exercise
def get_category_type(row):
    'A function that extracts the category of the venue in FourSquare JSON'
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']


# Get relevant part of FourSquare's explore call JSON
items = results['response']['groups'][0]['items']

dataframe = json_normalize(items) # flatten JSON

# Filter columns
filtered_columns = ['venue.name', 'venue.categories'] + [col for col in dataframe.columns if col.startswith('venue.location.')] + ['venue.id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# Filter the category for each row
dataframe_filtered['venue.categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# Clean columns
dataframe_filtered.columns = [col.split('.')[-1] for col in dataframe_filtered.columns]

dataframe_filtered.head(10)

name             categories  \
0                                  Roemah Noni  Indonesian Restaurant   
1                                    Starbucks            Coffee Shop   
2  Focus Nusantara - Camera & Photography Shop           Camera Store   
3                                RM. Adem Ayem  Indonesian Restaurant   
4                            McDonald's Cideng   Fast Food Restaurant   
5              Ibis Budget Jakarta Tanah Abang        Vacation Rental   
6                                     Beautika  Manadonese Restaurant   
7                              Bubur Ayam Musi         Breakfast Spot   
8                                 Petrof Piano            Music Venue   
9                        Wita Tour Head Office                 Office   

                       address       lat         lng  \
0         Jl. Kesehatan No. 12 -6.172590  106.815097   
1  Jalan Tanah Abang II No. 76 -6.175441  106.812220   
2          Tanah Abang II No.7 -6.175639  106.812901   
3            Jl. AM Sangaji 27 -6.168778  106.814470   
4                   Jl. Cideng -6.173391  106.811314   
5   Jalan Tanah Abang II No.35 -6.175735  106.816305   
6       Jl. Abdul Muis No. 70A -6.179549  106.818076   
7                  Jl. Musi 19 -6.174420  106.809554   
8                       Cideng -6.172733  106.811713   
9          Jl. Balikpapan No.5 -6.170505  106.814110   

                                      labeledLatLngs  distance   postalCode  \
0  [{'label': 'display', 'lat': -6.17258972867655...        81  DKI Jakarta   
1  [{'label': 'display', 'lat': -6.175441, 'lng':...       472        10160   
2  [{'label': 'display', 'lat': -6.17563886742587...       428          NaN   
3  [{'label': 'display', 'lat': -6.16877788919146...       488          NaN   
4  [{'label': 'display', 'lat': -6.17339057589308...       488          NaN   
5  [{'label': 'display', 'lat': -6.17573545874999...       312        10160   
6  [{'label': 'display', 'lat': -6.17954884800084...       775          NaN   
7  [{'label': 'display', 'lat': -6.17441955029394...       699          NaN   
8  [{'label': 'display', 'lat': -6.17273256156308...       443          NaN   
9  [{'label': 'display', 'lat': -6.17050476836452...       328          NaN   

   cc           city    state    country  \
0  ID  Jakarta Barat  Jakarta  Indonesia   
1  ID  Jakarta Pusat  Jakarta  Indonesia   
2  ID        Jakarta  Jakarta  Indonesia   
3  ID        Jakarta  Jakarta  Indonesia   
4  ID  Jakarta Pusat  Jakarta  Indonesia   
5  ID  Jakarta Pusat  Jakarta  Indonesia   
6  ID  Jakarta Pusat  Jakarta  Indonesia   
7  ID        Jakarta  Jakarta  Indonesia   
8  ID        Jakarta  Jakarta  Indonesia   
9  ID  Jakarta Pusat  Jakarta  Indonesia   

                                    formattedAddress  \
0  [Jl. Kesehatan No. 12, Jakarta, Jakarta DKI Ja...   
1  [Jalan Tanah Abang II No. 76 (Jalan Cideng Tim...   
2  [Tanah Abang II No.7, Jakarta, Jakarta, Indone...   
3   [Jl. AM Sangaji 27, Jakarta, Jakarta, Indonesia]   
4    [Jl. Cideng, Jakarta Pusat, Jakarta, Indonesia]   
5  [Jalan Tanah Abang II No.35 (Jalan Kesehatan),...   
6  [Jl. Abdul Muis No. 70A (Jalan Tanah Abang 5),...   
7  [Jl. Musi 19 (Depan gereja GPIB Petrus Musi), ...   
8              [Cideng, Jakarta, Jakarta, Indonesia]   
9  [Jl. Balikpapan No.5, Jakarta Pusat, Jakarta, ...   

                     crossStreet neighborhood                        id  
0                            NaN          NaN  4c9598ba03413704bda47def  
1             Jalan Cideng Timur          NaN  4e500fd81fc7e04d29e3287e  
2                            NaN          NaN  4ef30c5930f8e7873c876660  
3                            NaN          NaN  4ca5810a76d3a093f9c5f86a  
4                            NaN          NaN  54460633498e1a99f7831268  
5                Jalan Kesehatan          NaN  57bcfedf498eb883b3f76285  
6            Jalan Tanah Abang 5          NaN  4e34fbb9fa7656ba316c914e  
7  Depan gereja GPIB Petrus Musi          NaN  4bcf9f7846

Visualize venues around the subdistrict to verify.

In [12]:
# Generate map centred around Gambir
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) 

# Add center of Gambir subdistrict as a red circle mark
folium.CircleMarker(
    [latitude, longitude],
    radius=10,
    popup='Gambir',
    fill=True,
    color='red',
    fill_color='red',
    fill_opacity=0.6
    ).add_to(venues_map)


# Add popular spots to the map as blue circle markers
for lat, lng, cat, venue in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories, dataframe_filtered.name):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup= venue + ", " + cat,
        fill=True,
        color='blue',
        fill_color='blue',
        fill_opacity=0.6
        ).add_to(venues_map)

# display map
venues_map

The venue distribution looks good. Keep in mind that there is a limit of 100 venues for FourSquare API calls.

Now to get all the venues from each subdistricts.

In [13]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    '''
    A function to pull nearby venues for each of the subdistricts
    Adapted from previous exercise
    '''
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Subdistrict', 
                  'Subdistrict Latitude', 
                  'Subdistrict Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Call the function to make the repeated query.

In [14]:
jakarta_venues_cat = getNearbyVenues(names=jakarta_df['Subdistrict'],
                                 latitudes=jakarta_df['Latitude'],
                                 longitudes=jakarta_df['Longitude'],
                                 radius = 1500)

jakarta_venues_cat.head(10)

Cengkareng
Grogol Petamburan
Kalideres
Kebon Jeruk
Kembangan
Palmerah
Taman Sari
Tambora
Cempaka Putih
Gambir
Johar Baru
Kemayoran
Sawah Besar
Senen
Tanah Abang
Cilandak
Jagakarsa
Kebayoran Baru
Kebayoran Lama
Mampang Prapatan
Pancoran
Pasar Minggu
Pesanggrahan
Setiabudi
Tebet
Cakung
Cipayung
Ciracas
Duren Sawit
Jatinegara
Kramat Jati
Makasar
Matraman
Menteng
Pasar Rebo
Pulo Gadung
Cilincing
Kelapa Gading
Koja
Pademangan
Penjaringan
Tanjung Priok


Subdistrict  Subdistrict Latitude  Subdistrict Longitude  \
0  Cengkareng               -6.1306              106.74559   
1  Cengkareng               -6.1306              106.74559   
2  Cengkareng               -6.1306              106.74559   
3  Cengkareng               -6.1306              106.74559   
4  Cengkareng               -6.1306              106.74559   
5  Cengkareng               -6.1306              106.74559   
6  Cengkareng               -6.1306              106.74559   
7  Cengkareng               -6.1306              106.74559   
8  Cengkareng               -6.1306              106.74559   
9  Cengkareng               -6.1306              106.74559   

                           Venue  Venue Latitude  Venue Longitude  \
0   Ikana - Ikana Seafood & Cafe       -6.124557       106.749859   
1                      Bakso Aan       -6.123921       106.743012   
2  MYSTIQUE Pool - Lounge - Dine       -6.123594       106.740567   
3                    Fins Recipe       -6.124033       106.743319   
4            Bakmi pejagalan AMI       -6.128617       106.754013   
5                    MeaterS PIK       -6.123683       106.741391   
6       Bakmi Bintang Gading PIK       -6.123673       106.741235   
7            PVBLIC Bistro & BAR       -6.123571       106.738523   
8             Uncle Tjhin Bistro       -6.123666       106.741271   
9                     Tea Garden       -6.132895       106.734944   

       Venue Category  
0  Seafood Restaurant  
1    Asian Restaurant  
2          Sports Bar  
3        Dessert Shop  
4        Noodle House  
5          Steakhouse  
6        Noodle House  
7                 Bar  
8              Bistro  
9    Asian Restaurant

Check the resulting data frame size and content.

In [15]:
print("Shape of df:",jakarta_venues_cat.shape)
jakarta_venues_cat.head()

Shape of df: (2968, 7)


Subdistrict  Subdistrict Latitude  Subdistrict Longitude  \
0  Cengkareng               -6.1306              106.74559   
1  Cengkareng               -6.1306              106.74559   
2  Cengkareng               -6.1306              106.74559   
3  Cengkareng               -6.1306              106.74559   
4  Cengkareng               -6.1306              106.74559   

                           Venue  Venue Latitude  Venue Longitude  \
0   Ikana - Ikana Seafood & Cafe       -6.124557       106.749859   
1                      Bakso Aan       -6.123921       106.743012   
2  MYSTIQUE Pool - Lounge - Dine       -6.123594       106.740567   
3                    Fins Recipe       -6.124033       106.743319   
4            Bakmi pejagalan AMI       -6.128617       106.754013   

       Venue Category  
0  Seafood Restaurant  
1    Asian Restaurant  
2          Sports Bar  
3        Dessert Shop  
4        Noodle House

Check how many venues were returned for each subdistrict.

In [16]:
jakarta_venues_cat.groupby('Subdistrict').count()

Subdistrict Latitude  Subdistrict Longitude  Venue  \
Subdistrict                                                             
Cakung                                7                      7      7   
Cempaka Putih                       100                    100    100   
Cengkareng                           32                     32     32   
Cilandak                            100                    100    100   
Cilincing                             7                      7      7   
Cipayung                             11                     11     11   
Ciracas                              29                     29     29   
Duren Sawit                          55                     55     55   
Gambir                              100                    100    100   
Grogol Petamburan                   100                    100    100   
Jagakarsa                            12                     12     12   
Jatinegara                           65                     65     65   
Johar Baru                           59                     59     59   
Kalideres                            62                     62     62   
Kebayoran Baru                      100                    100    100   
Kebayoran Lama                      100                    100    100   
Kebon Jeruk                         100                    100    100   
Kelapa Gading                       100                    100    100   
Kemayoran                            46                     46     46   
Kembangan                            14                     14     14   
Koja                                 15                     15     15   
Kramat Jati                          41                     41     41   
Makasar                              36                     36     36   
Mampang Prapatan                     82                     82     82   
Matraman                             95                     95     95   
Menteng                             100                    100    100   
Pademangan                          100                    100    100   
Palmerah                            100                    100    100   
Pancoran                            100                    100    100   
Pasar Minggu                         57                     57     57   
Pasar Rebo                           18                     18     18   
Penjaringan                         100                    100    100   
Pesanggrahan                         37                     37     37   
Pulo Gadung                         100                    100    100   
Sawah Besar                         100                    100    100   
Senen                               100                    100    100   
Setiabudi                           100                    100    100   
Taman Sari                          100                    100    100   
Tambora                             100                    100    100   
Tanah Abang                         100                    100    100   
Tanjung Priok                        88                     88     88   
Tebet                               100                    100    100   

                   Venue Latitude  Venue Longitude  Venue Category  
Subdistrict                                                         
Cakung                          7                7               7  
Cempaka Putih                 100              100             100  
Cengkareng                     32               32              32  
Cilandak                      100              100             100  
Cilincing                       7                7               7  
Cipayung                       11               11              11  
Ciracas                        29               29              29  
Duren Sawit                    55               55              55  
Gambir                        100              100             100  
Grogol Petamburan             100              

Drop subdistrict with less than 10 venues. These sub-districts are considered to be not popular for our purpose.

In [17]:
# Filter subdistrict
lowvenue_subdistrict = jakarta_venues_cat.groupby('Subdistrict').Venue.count() < 10
lowvenue_subdistrict = list(lowvenue_subdistrict[lowvenue_subdistrict].index)

# duplicate df
jakarta_venues = jakarta_venues_cat

# Exclude the subdistricts
for i in lowvenue_subdistrict:
    jakarta_venues = jakarta_venues[jakarta_venues.Subdistrict != i]

Recheck how many venues were returned for each subdistrict.

In [18]:
jakarta_venues.groupby('Subdistrict').count()

Subdistrict Latitude  Subdistrict Longitude  Venue  \
Subdistrict                                                             
Cempaka Putih                       100                    100    100   
Cengkareng                           32                     32     32   
Cilandak                            100                    100    100   
Cipayung                             11                     11     11   
Ciracas                              29                     29     29   
Duren Sawit                          55                     55     55   
Gambir                              100                    100    100   
Grogol Petamburan                   100                    100    100   
Jagakarsa                            12                     12     12   
Jatinegara                           65                     65     65   
Johar Baru                           59                     59     59   
Kalideres                            62                     62     62   
Kebayoran Baru                      100                    100    100   
Kebayoran Lama                      100                    100    100   
Kebon Jeruk                         100                    100    100   
Kelapa Gading                       100                    100    100   
Kemayoran                            46                     46     46   
Kembangan                            14                     14     14   
Koja                                 15                     15     15   
Kramat Jati                          41                     41     41   
Makasar                              36                     36     36   
Mampang Prapatan                     82                     82     82   
Matraman                             95                     95     95   
Menteng                             100                    100    100   
Pademangan                          100                    100    100   
Palmerah                            100                    100    100   
Pancoran                            100                    100    100   
Pasar Minggu                         57                     57     57   
Pasar Rebo                           18                     18     18   
Penjaringan                         100                    100    100   
Pesanggrahan                         37                     37     37   
Pulo Gadung                         100                    100    100   
Sawah Besar                         100                    100    100   
Senen                               100                    100    100   
Setiabudi                           100                    100    100   
Taman Sari                          100                    100    100   
Tambora                             100                    100    100   
Tanah Abang                         100                    100    100   
Tanjung Priok                        88                     88     88   
Tebet                               100                    100    100   

                   Venue Latitude  Venue Longitude  Venue Category  
Subdistrict                                                         
Cempaka Putih                 100              100             100  
Cengkareng                     32               32              32  
Cilandak                      100              100             100  
Cipayung                       11               11              11  
Ciracas                        29               29              29  
Duren Sawit                    55               55              55  
Gambir                        100              100             100  
Grogol Petamburan             100              100             100  
Jagakarsa                      12               12              12  
Jatinegara                     65               65              65  
Johar Baru                     59               59              59  
Kalideres                      62               62     

Check the number of unique categories.

In [19]:
print('There are {} uniques categories.'.format(len(jakarta_venues['Venue Category'].unique())))

There are 252 uniques categories.


Visualize the venues on the map.

In [20]:
jktmap_venue = folium.Map(location=jakarta["DKI Jakarta"], zoom_start=11) # generate map centred around the Conrad Hotel

# add a red circle marker to represent center of Jakarta
folium.CircleMarker(
    jakarta["DKI Jakarta"],
    radius=10,
    color='red',
    popup='Jakarta',
    fill = True,
    fill_color = 'red',
    fill_opacity = 1
    ).add_to(jktmap_venue)

# add the subdistritcs as blue circle markers
for subdist, coord in subdistcoord.items():
    folium.CircleMarker(
        coord,
        radius=5,
        color='blue',
        popup=subdist,
        fill = True,
        fill_color='blue',
        fill_opacity=1
    ).add_to(jktmap_venue)

# add venues to the map as green circle markers
for lat, lng, label, cat in zip(jakarta_venues["Venue Latitude"], jakarta_venues["Venue Longitude"], 
                                jakarta_venues["Venue"], jakarta_venues["Venue Category"]):
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label +", " + cat,
        fill=True,
        color='green',
        fill_color='green',
        fill_opacity=0.6
        ).add_to(jktmap_venue)


# display map
jktmap_venue

As can be seen from the clustering, there is a big skew on central Jakarta.

Also, the two excluded subdistrict is located quite far off the city center. It should be confirmed to be save for exclusion.

# Methodology<a id='methodology'></a>

Given that our objective is to generally categorize the subdistricts, we will use K-means clustering algorithm to categorize each of the subdistricts within Jakarta.

A one-hot encoding will be done on the venue dataframe and it will be grouped by subdistrict. The encoding will return venue categories as column per subdistrict, which will then be grouped to provide weighting of venue type occurence on each subdistrict.

The encoded dataframe will be further filtered into top venues before the K-means clustering algorithm will be run over it. This will return cluster labels over the subdistricts. The clusters will be observed one by one manually to determine its content.

Recommendation will be made based on the clusterring.

# Analysis<a id='analysis'></a>

Apply one-hot encoding to the dataframe.

In [21]:
# one hot encoding
jakarta_onehot = pd.get_dummies(jakarta_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
jakarta_onehot['Subdistrict'] = jakarta_venues['Subdistrict'] 

# move neighborhood column to the first column
fixed_columns = [jakarta_onehot.columns[-1]] + list(jakarta_onehot.columns[:-1])
jakarta_onehot = jakarta_onehot[fixed_columns]

jakarta_onehot.head()

Subdistrict  Accessories Store  Acehnese Restaurant  African Restaurant  \
0  Cengkareng                  0                    0                   0   
1  Cengkareng                  0                    0                   0   
2  Cengkareng                  0                    0                   0   
3  Cengkareng                  0                    0                   0   
4  Cengkareng                  0                    0                   0   

   Airport  American Restaurant  Aquarium  Arcade  Art Gallery  Art Museum  \
0        0                    0         0       0            0           0   
1        0                    0         0       0            0           0   
2        0                    0         0       0            0           0   
3        0                    0         0       0            0           0   
4        0                    0         0       0            0           0   

   ...  Vegetarian / Vegan Restaurant  Veterinarian  Video Game Store  \
0  ...                              0             0                 0   
1  ...                              0             0                 0   
2  ...                              0             0                 0   
3  ...                              0             0                 0   
4  ...                              0             0                 0   

   Vietnamese Restaurant  Water Park  Wine Bar  Winery  Wings Joint  \
0                      0           0         0       0            0   
1                      0           0         0       0            0   
2                      0           0         0       0            0   
3                      0           0         0       0            0   
4                      0           0         0       0            0   

   Women's Store  Yoga Studio  
0              0            0  
1              0            0  
2              0            0  
3              0            0  
4              0            0  

[5 rows x 253 columns]

Check shape.

In [22]:
jakarta_onehot.shape

(2954, 253)

Group the encoded dataframe.

In [23]:
jakarta_grouped = jakarta_onehot.groupby('Subdistrict').mean().reset_index()
jakarta_grouped

Subdistrict  Accessories Store  Acehnese Restaurant  \
0       Cempaka Putih               0.00             0.010000   
1          Cengkareng               0.00             0.000000   
2            Cilandak               0.00             0.000000   
3            Cipayung               0.00             0.000000   
4             Ciracas               0.00             0.000000   
5         Duren Sawit               0.00             0.000000   
6              Gambir               0.00             0.000000   
7   Grogol Petamburan               0.00             0.000000   
8           Jagakarsa               0.00             0.000000   
9          Jatinegara               0.00             0.000000   
10         Johar Baru               0.00             0.000000   
11          Kalideres               0.00             0.000000   
12     Kebayoran Baru               0.00             0.000000   
13     Kebayoran Lama               0.00             0.000000   
14        Kebon Jeruk               0.00             0.000000   
15      Kelapa Gading               0.00             0.000000   
16          Kemayoran               0.00             0.000000   
17          Kembangan               0.00             0.000000   
18               Koja               0.00             0.000000   
19        Kramat Jati               0.00             0.000000   
20            Makasar               0.00             0.000000   
21   Mampang Prapatan               0.00             0.012195   
22           Matraman               0.00             0.000000   
23            Menteng               0.00             0.000000   
24         Pademangan               0.01             0.000000   
25           Palmerah               0.00             0.000000   
26           Pancoran               0.00             0.010000   
27       Pasar Minggu               0.00             0.017544   
28         Pasar Rebo               0.00             0.000000   
29        Penjaringan               0.00             0.000000   
30       Pesanggrahan               0.00             0.000000   
31        Pulo Gadung               0.00             0.000000   
32        Sawah Besar               0.00             0.000000   
33              Senen               0.00             0.000000   
34          Setiabudi               0.00             0.000000   
35         Taman Sari               0.00             0.000000   
36            Tambora               0.00             0.000000   
37        Tanah Abang               0.00             0.000000   
38      Tanjung Priok               0.00             0.000000   
39              Tebet               0.00             0.010000   

    African Restaurant   Airport  American Restaurant  Aquarium    Arcade  \
0                 0.00  0.000000             0.000000      0.00  0.000000   
1                 0.00  0.000000             0.031250      0.00  0.000000   
2                 0.00  0.000000             0.000000      0.00  0.000000   
3                 0.00  0.000000             0.000000      0.00  0.000000   
4                 0.00  0.000000             0.034483      0.00  0.000000   
5                 0.00  0.000000             0.000000      0.00  0.000000   
6                 0.00  0.000000             0.000000      0.00  0.000000   
7                 0.00  0.000000             0.000000      0.01  0.000000   
8                 0.00  0.000000             0.000000      0.00  0.000000   
9                 0.00  0.015385             0.000000      0.00  0.000000   
10                0.00  0.000000             0.000000      0.00  0.016949   
11                0.00  0.000000             0.000000      0.00  0.000000   
12                0.00  0.000000             0.010000      0.00  0.000000   
13                0.00  0.000000             0.020000      0.00  0.010000   
14                0.00  0.000000             0.010000      0.00  0.010000   
15                0.01  0.000000             0.020000      0.00  0.010000   
16                0.00  0.021739   

In [24]:
jakarta_grouped.shape

(40, 253)

In [25]:
num_top_venues = 5

for hood in jakarta_grouped['Subdistrict']:
    print("----"+hood+"----")
    temp = jakarta_grouped[jakarta_grouped['Subdistrict'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Cempaka Putih----
                   venue  freq
0  Indonesian Restaurant  0.10
1            Pizza Place  0.08
2            Coffee Shop  0.06
3   Fast Food Restaurant  0.06
4                   Café  0.05


----Cengkareng----
              venue  freq
0  Asian Restaurant  0.09
1      Noodle House  0.09
2               Bar  0.06
3              Café  0.06
4       Pizza Place  0.06


----Cilandak----
                   venue  freq
0            Coffee Shop  0.10
1  Indonesian Restaurant  0.06
2       Asian Restaurant  0.06
3             Food Truck  0.06
4                   Café  0.06


----Cipayung----
                   venue  freq
0  Indonesian Restaurant  0.18
1       Asian Restaurant  0.09
2                 Garden  0.09
3          Grocery Store  0.09
4             Food Truck  0.09


----Ciracas----
                   venue  freq
0  Indonesian Restaurant   0.1
1       Asian Restaurant   0.1
2   Fast Food Restaurant   0.1
3            Coffee Shop   0.1
4           Noodle House   0.1



Define a function to return the most common venues.

In [26]:
# Adapted from previous exercise
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Create a new dataframe and display the top 10 venues for each neighborhood.

In [27]:
# Adapted from previous exercise
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Subdistrict']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Subdistrict'] = jakarta_grouped['Subdistrict']

for ind in np.arange(jakarta_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(jakarta_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Subdistrict  1st Most Common Venue 2nd Most Common Venue  \
0  Cempaka Putih  Indonesian Restaurant           Pizza Place   
1     Cengkareng       Asian Restaurant          Noodle House   
2       Cilandak            Coffee Shop            Food Truck   
3       Cipayung  Indonesian Restaurant     Food & Drink Shop   
4        Ciracas   Fast Food Restaurant      Asian Restaurant   

  3rd Most Common Venue  4th Most Common Venue  5th Most Common Venue  \
0  Fast Food Restaurant            Coffee Shop                   Café   
1                  Café  Indonesian Restaurant                 Bistro   
2      Asian Restaurant                   Café  Indonesian Restaurant   
3          Noodle House            High School            Pizza Place   
4          Noodle House  Indonesian Restaurant            Coffee Shop   

  6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
0                 Hotel  Indonesian Meatball Place            Restaurant   
1                   Bar                Pizza Place        Clothing Store   
2  Fast Food Restaurant                 Steakhouse       Motorcycle Shop   
3      Asian Restaurant              Grocery Store     Convenience Store   
4     Convenience Store             Farmers Market                Bakery   

  9th Most Common Venue 10th Most Common Venue  
0      Asian Restaurant            Flea Market  
1           Coffee Shop     Seafood Restaurant  
2    Chinese Restaurant                 Bakery  
3                Garden             Food Truck  
4           High School    Dumpling Restaurant

## Cluster Subdistricts

Run *k*-means to cluster the neighborhood into 5 clusters.

In [28]:
# set number of clusters
kclusters = 5

jakarta_grouped_clustering = jakarta_grouped.drop('Subdistrict', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(jakarta_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 1, 0, 0, 3, 1, 4, 3, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [29]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

jakarta_merged = jakarta_df

# drop NA from the excluded subdistrict
for i in lowvenue_subdistrict:
    jakarta_merged = jakarta_merged[jakarta_merged.Subdistrict != i]

# merge df to add latitude/longitude for each subdistrict
jakarta_merged = jakarta_merged.join(neighborhoods_venues_sorted.set_index('Subdistrict'), on='Subdistrict')

# Shift label to start from index 1
jakarta_merged['Cluster Labels'] = jakarta_merged['Cluster Labels'] + 1

jakarta_merged.head()

Subdistrict  Latitude  Longitude  Cluster Labels  \
0         Cengkareng  -6.13060  106.74559               2   
1  Grogol Petamburan  -6.16777  106.78457               5   
2          Kalideres  -6.12210  106.70727               2   
3        Kebon Jeruk  -6.19702  106.77308               2   
4          Kembangan  -6.21823  106.73749               4   

  1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
0      Asian Restaurant          Noodle House                   Café   
1          Noodle House           Coffee Shop     Chinese Restaurant   
2          Noodle House           Coffee Shop            Pizza Place   
3      Asian Restaurant     Convenience Store  Indonesian Restaurant   
4     Convenience Store            Food Court       Department Store   

   4th Most Common Venue  5th Most Common Venue  6th Most Common Venue  \
0  Indonesian Restaurant                 Bistro                    Bar   
1         Clothing Store     Seafood Restaurant  Indonesian Restaurant   
2       Asian Restaurant     Chinese Restaurant                   Café   
3            Coffee Shop             Steakhouse            Pizza Place   
4                   Park  Indonesian Restaurant            Music Venue   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0           Pizza Place        Clothing Store           Coffee Shop   
1            Steakhouse      Asian Restaurant            Restaurant   
2            Food Truck     Convenience Store   Japanese Restaurant   
3  Fast Food Restaurant          Noodle House                  Café   
4                   Spa                 Plaza   Japanese Restaurant   

  10th Most Common Venue  
0     Seafood Restaurant  
1       Sushi Restaurant  
2   Fast Food Restaurant  
3     Seafood Restaurant  
4            Snack Place

Visualize the resulting clusters

In [30]:
# create map
map_clusters = folium.Map(location=jakarta["DKI Jakarta"], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(jakarta_merged['Latitude'], jakarta_merged['Longitude'], jakarta_merged['Subdistrict'], jakarta_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## Examine Clusters

Examine each clusters.

#### Cluster 1

Cluster 1 contains a concentration of noodle house and other asian restaurant. Geographically, they are all located at the south east corner of the city with golf course as one of its common venue. Seems like this cluster revolves around the golf course.

In [31]:
jakarta_merged.loc[jakarta_merged['Cluster Labels'] == 1, jakarta_merged.columns[[0] + list(range(4, jakarta_merged.shape[1]))]]

Subdistrict  1st Most Common Venue  2nd Most Common Venue  \
26    Cipayung  Indonesian Restaurant      Food & Drink Shop   
27     Ciracas   Fast Food Restaurant       Asian Restaurant   
31     Makasar            Golf Course  Indonesian Restaurant   

   3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
26          Noodle House            High School           Pizza Place   
27          Noodle House  Indonesian Restaurant           Coffee Shop   
31  Fast Food Restaurant            Pizza Place          Noodle House   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
26      Asian Restaurant         Grocery Store     Convenience Store   
27     Convenience Store        Farmers Market                Bakery   
31      Asian Restaurant      Department Store         Shopping Mall   

   9th Most Common Venue 10th Most Common Venue  
26                Garden             Food Truck  
27           High School    Dumpling Restaurant  
31           Supermarket              Bookstore

#### Cluster 2

With the most member, cluster 2 seems to contain a good amount of Coffee shop and hotels. Located central-south of the city, it is expected to have a high concentration of places to hang out and stay.

In [32]:
jakarta_merged.loc[jakarta_merged['Cluster Labels'] == 2, jakarta_merged.columns[[0] + list(range(4, jakarta_merged.shape[1]))]]

Subdistrict  1st Most Common Venue  2nd Most Common Venue  \
0         Cengkareng       Asian Restaurant           Noodle House   
2          Kalideres           Noodle House            Coffee Shop   
3        Kebon Jeruk       Asian Restaurant      Convenience Store   
5           Palmerah            Coffee Shop       Asian Restaurant   
8      Cempaka Putih  Indonesian Restaurant            Pizza Place   
9             Gambir                  Hotel  Indonesian Restaurant   
10        Johar Baru  Indonesian Restaurant                  Hotel   
11         Kemayoran                  Hotel  Indonesian Restaurant   
13             Senen  Indonesian Restaurant            Coffee Shop   
14       Tanah Abang            Coffee Shop                  Hotel   
15          Cilandak            Coffee Shop             Food Truck   
17    Kebayoran Baru            Coffee Shop    Japanese Restaurant   
18    Kebayoran Lama            Coffee Shop         Clothing Store   
19  Mampang Prapatan            Coffee Shop             Restaurant   
20          Pancoran            Coffee Shop                   Café   
21      Pasar Minggu  Indonesian Restaurant            Coffee Shop   
23         Setiabudi            Coffee Shop                  Hotel   
24             Tebet  Indonesian Restaurant            Coffee Shop   
29        Jatinegara            Coffee Shop  Indonesian Restaurant   
30       Kramat Jati  Indonesian Restaurant   Fast Food Restaurant   
32          Matraman  Indonesian Restaurant       Asian Restaurant   
33           Menteng  Indonesian Restaurant                  Hotel   
37     Kelapa Gading            Coffee Shop  Indonesian Restaurant   

        3rd Most Common Venue  4th Most Common Venue   5th Most Common Venue  \
0                        Café  Indonesian Restaurant                  Bistro   
2                 Pizza Place       Asian Restaurant      Chinese Restaurant   
3       Indonesian Restaurant            Coffee Shop              Steakhouse   
5       Indonesian Restaurant                  Hotel              Food Truck   
8        Fast Food Restaurant            Coffee Shop                    Café   
9                 Coffee Shop     Seafood Restaurant        Asian Restaurant   
10                Pizza Place               Pharmacy  Furniture / Home Store   
11  Indonesian Meatball Place       Asian Restaurant              Food Court   
13                      Hotel                   Café    Fast Food Restaurant   
14      Indonesian Restaurant    Japanese Restaurant              Restaurant   
15           Asian Restaurant                   Café   Indonesian Restaurant   
17      Indonesian Restaurant             Food Truck               BBQ Joint   
18      Indonesian Restaurant                   Café             Pizza Place   
19                      Hotel             Food Truck        Asian Restaurant   
20           Asian Restaurant      Convenience Store   Indonesian Restaurant   
21                 Food Truck    Japanese Restaurant          Breakfast Spot   
23         Italian Restaurant  Indonesian Restaurant      Chinese Restaurant   
24             Clothing Store                   Café                  Bakery   
29           Asian Restaurant   Fast Food Restaurant                    Café   
30                 Donut Shop              BBQ Joint              Restaurant   
32                Pizza Place      Convenience Store             Coffee Shop   
33                Coffee Shop                   Café   Betawinese Restaurant   
37               Noodle House       Asian Restaurant                  Bakery   

   6th Most Common Venue      7th Most Common Venue  \
0                    Bar                Pizza Place   
2                   Café                 Food Truck   
3            Pizza Place       Fast Food Restaurant   
5      Convenience Store                       Café   
8                  Hotel  Indonesian Meatball Place   
9           Camera Store               Noodle House   
10    Seafood Restaura

#### Cluster 3

Containing only 1 subdistrict, cluster 3 seems to be in its own group located at the north east of the city. This might be due to the low count of trending venues of 15. Nothing much can be gathered from this cluster.

In [33]:
jakarta_merged.loc[jakarta_merged['Cluster Labels'] == 3, jakarta_merged.columns[[0] + list(range(4, jakarta_merged.shape[1]))]]

Subdistrict  1st Most Common Venue      2nd Most Common Venue  \
38        Koja  Indonesian Restaurant  Indonesian Meatball Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
38           Pizza Place            Restaurant     Convenience Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
38                Bakery           High School   Government Building   

   9th Most Common Venue 10th Most Common Venue  
38        Cosmetics Shop             Art Museum

#### Cluster 4

Having commonality with cluster 3 with Indonesian restaurants as its common venue, cluster 4 have higher count of convenience store in general. The subdistricts within this cluster are more scatered, being dispersed on around the border surrounding cluster 2

In [34]:
jakarta_merged.loc[jakarta_merged['Cluster Labels'] == 4, jakarta_merged.columns[[0] + list(range(4, jakarta_merged.shape[1]))]]

Subdistrict      1st Most Common Venue 2nd Most Common Venue  \
4      Kembangan          Convenience Store            Food Court   
16     Jagakarsa          Convenience Store      Department Store   
22  Pesanggrahan                 Food Truck          Noodle House   
28   Duren Sawit  Indonesian Meatball Place  Fast Food Restaurant   
34    Pasar Rebo      Indonesian Restaurant         Grocery Store   

     3rd Most Common Venue  4th Most Common Venue  5th Most Common Venue  \
4         Department Store                   Park  Indonesian Restaurant   
16  College Residence Hall           Noodle House           Burger Joint   
22    Fast Food Restaurant  Indonesian Restaurant      Convenience Store   
28              Food Truck           Noodle House      Convenience Store   
34                 Factory             Food Court   Fast Food Restaurant   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
4            Music Venue                   Spa                  Plaza   
16  Other Great Outdoors          Soccer Field   Fast Food Restaurant   
22            Food Court                  Café          Grocery Store   
28    Salon / Barbershop        Ice Cream Shop  Indonesian Restaurant   
34                Bakery    Seafood Restaurant                   Café   

   9th Most Common Venue     10th Most Common Venue  
4    Japanese Restaurant                Snack Place  
16    Seafood Restaurant                 Food Truck  
22     Electronics Store  Indonesian Meatball Place  
28      Asian Restaurant         Seafood Restaurant  
34                  Food           Baseball Stadium

#### Cluster 5

Cluster 5 contains a higher concentration of noodle house and chinese restaurant. Located north of Jakarta, this might be the cluster for Chinese restaurants.

In [35]:
jakarta_merged.loc[jakarta_merged['Cluster Labels'] == 5, jakarta_merged.columns[[0] + list(range(4, jakarta_merged.shape[1]))]]

Subdistrict 1st Most Common Venue  2nd Most Common Venue  \
1   Grogol Petamburan          Noodle House            Coffee Shop   
6          Taman Sari    Chinese Restaurant           Noodle House   
7             Tambora    Chinese Restaurant           Noodle House   
12        Sawah Besar    Chinese Restaurant           Noodle House   
35        Pulo Gadung          Noodle House  Indonesian Restaurant   
39         Pademangan    Seafood Restaurant                  Hotel   
40        Penjaringan    Seafood Restaurant     Chinese Restaurant   
41      Tanjung Priok      Asian Restaurant           Noodle House   

   3rd Most Common Venue  4th Most Common Venue  5th Most Common Venue  \
1     Chinese Restaurant         Clothing Store     Seafood Restaurant   
6       Asian Restaurant                  Hotel     Seafood Restaurant   
7       Asian Restaurant                  Hotel            Coffee Shop   
12                 Hotel            Coffee Shop  Indonesian Restaurant   
35           Coffee Shop             Food Truck     Chinese Restaurant   
39          Noodle House     Chinese Restaurant            Coffee Shop   
40          Noodle House            Coffee Shop                   Café   
41    Chinese Restaurant  Indonesian Restaurant            Pizza Place   

    6th Most Common Venue  7th Most Common Venue  \
1   Indonesian Restaurant             Steakhouse   
6                  Bakery            Coffee Shop   
7                  Bakery  Indonesian Restaurant   
12     Seafood Restaurant                   Café   
35       Asian Restaurant                   Café   
39             Theme Park       Asian Restaurant   
40                 Bakery  Indonesian Restaurant   
41                   Café                  Beach   

           8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
1               Asian Restaurant             Restaurant       Sushi Restaurant  
6           Fast Food Restaurant              Hotel Bar             Steakhouse  
7                     Food Truck         Massage Studio             Steakhouse  
12         Padangnese Restaurant             Restaurant             Steakhouse  
35                    Soup Place     Seafood Restaurant      Convenience Store  
39  Theme Park Ride / Attraction  Indonesian Restaurant             Food Truck  
40                    Restaurant    Balinese Restaurant       Asian Restaurant  
41            Seafood Restaurant   Fast Food Restaurant         Massage Studio

# Result and Discussion<a id='results'></a>

Groupings as a result of K-means clustering algorithm tallies with how Jakarta historically develops. Having most of cluster 5, containing a high count of chinese restaurant, at the north side of the city fits the chinatown part of the city. Cluster 2 being the dominant type of subdistrict which is located in the middle also fits the reality. North eastern part being quite sparse in trending venue also fits the reality that the area is more of an industrial area, thus having less venues.

There are definite limitation with using the FourSquare API as the 100 venues limit might skew the result of the more densely populated subdistrict. Also, some subdistricts have low count of venues that it might be considered to be insufficient in determining its characteristics. It might also be the case that FourSquare user base are skewed to the foodie type, which might explain the limited trending venues on the North east part of the city.

For most of the subdistricts, restaurants and coffee shops are the dominant venue type with cluster 2 having more variation in terms of cuisine.

# Conclusion<a id='conclusion'></a>

Opening of new western restaurant may be best done in cluster 5 where there are less of such restaurant to compete. Business which does not rely on foot traffic may choose to locate themself in the north east of Jakarta.